## Step 1: Setup and Load Data

In [6]:
# Import libraries
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from datetime import datetime, timedelta
import warnings
warnings.filterwarnings('ignore')

# ML libraries
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
from sklearn.ensemble import RandomForestRegressor
import xgboost as xgb

print("All libraries imported successfully!")

All libraries imported successfully!


In [7]:
# Load merged data with external features
df = pd.read_csv("../data/processed/traffy_with_external.csv")

# Convert datetime columns
df['timestamp'] = pd.to_datetime(df['timestamp'], format='mixed')
df['last_activity'] = pd.to_datetime(df['last_activity'], format='mixed')

print(f"Dataset loaded: {len(df):,} rows")
print(f"Date range: {df['timestamp'].min()} to {df['timestamp'].max()}")

# Check external data availability
external_features = ['pm25_avg', 'rainfall_mm', 'is_holiday', 'is_weekend', 'weather_severity']
print(f"\n📊 External data coverage:")
for feat in external_features:
    if feat in df.columns:
        coverage = df[feat].notna().sum()
        print(f"  {feat}: {coverage:,} rows ({coverage/len(df)*100:.1f}%)")
    else:
        print(f"  {feat}: NOT FOUND")

print(f"\nTotal columns: {len(df.columns)}")
df.head()

Dataset loaded: 403,830 rows
Date range: 2021-09-03 12:51:09.453003+00:00 to 2023-10-24 08:09:29.128078+00:00

📊 External data coverage:
  pm25_avg: 403,818 rows (100.0%)
  rainfall_mm: 403,818 rows (100.0%)
  is_holiday: 403,818 rows (100.0%)
  is_weekend: 403,818 rows (100.0%)
  weather_severity: 403,818 rows (100.0%)

Total columns: 45


ticket_id                 type                      organization  \
0  2021-FYJTFP          {ความสะอาด}                        เขตบางซื่อ   
1  2021-CGPMUN  {น้ำท่วม,ร้องเรียน}      เขตประเวศ,ฝ่ายโยธา เขตประเวศ   
2  2021-7XATFA              {สะพาน}                           เขตสาทร   
3  2021-9U2NJT            {น้ำท่วม}    เขตบางซื่อ,ฝ่ายโยธา เขตบางซื่อ   
4  2021-DVEWYM        {น้ำท่วม,ถนน}  เขตลาดพร้าว,ฝ่ายโยธา เขตลาดพร้าว   

                                             comment  \
0                                            ขยะเยอะ   
1  น้ำท่วมเวลาฝนตกและทะลุเข้าบ้านเดือดร้อนมากทุกๆ...   
2    สะพานลอยปรับปรุงไม่เสร็จตามกำหนด\nปากซอย สาทร12   
3                                            น้ำท่วม   
4  ซอยลาดพร้าววังหิน 75 ถนนลาดพร้าววังหิน แขวงลาด...   

                                               photo  \
0  https://storage.googleapis.com/traffy_public_b...   
1  https://storage.googleapis.com/traffy_public_b...   
2  https://storage.googleapis.com/traffy_public_b...   
3  https://storage.googleapis.com/traffy_public_b...   
4  https://storage.googleapis.com/traffy_public_b...   

                                         photo_after              coords  \
0                                                NaN  100.53084,13.81865   
1  https://storage.googleapis.com/traffy_public_b...  100.66709,13.67891   
2                                                NaN  100.52649,13.72060   
3  https://storage.googleapis.com/traffy_public_b...  100.53099,13.81853   
4                                                NaN  100.59165,13.82280   

                                             address subdistrict  district  \
0  12/14 ถนน กรุงเทพ- นนทบุรี แขวง บางซื่อ เขตบาง...     บางซื่อ   บางซื่อ   
1  189 เฉลิมพระเกียรติ ร.9 แขวง หนองบอน เขต ประเว...     หนองบอน    ประเวศ   
2  191/1 ถนน สาทรเหนือ แขวง สีลม เขตบางรัก กรุงเท...     ยานนาวา      สาทร   
3  12/14 ถนน กรุงเทพ- นนทบุรี แขวง บางซื่อ เขตบาง...     บางซื่อ   บางซื่อ   
4  702 ถ. ลาดพร้าววังหิน แขวงลาดพร้าว เขตลาดพร้าว...    ลาดพร้าว  ลาดพร้าว   

   ... month_ext day_of_week_ext quarter  day_of_year is_weekend  is_holiday  \
0  ...       NaN             NaN     NaN          NaN        NaN         NaN   
1  ...       NaN             NaN     NaN          NaN        NaN         NaN   
2  ...       NaN             NaN     NaN          NaN        NaN         NaN   
3  ...       NaN             NaN     NaN          NaN        NaN         NaN   
4  ...       NaN             NaN     NaN          NaN        NaN         NaN   

   holiday  holiday_type  weather_severity  year_month  
0      NaN           NaN               NaN         NaN  
1      NaN           NaN               NaN         NaN  
2      NaN           NaN               NaN         NaN  
3      NaN           NaN               NaN         NaN  
4      NaN           NaN               NaN         NaN  

[5 rows x 45 columns]

## Step 2: Target Variable Creation
Calculate `resolution_time_hours` and filter for closed cases

In [8]:
# Filter only closed cases (state = เสร็จสิ้น)
df_closed = df[df['state'] == 'เสร็จสิ้น'].copy()

# Ensure resolution_time_hours exists and is valid
if 'resolution_time_hours' not in df_closed.columns:
    df_closed['resolution_time_hours'] = (df_closed['last_activity'] - df_closed['timestamp']).dt.total_seconds() / 3600

# Remove invalid cases (negative or extremely long resolution times)
df_closed = df_closed[
    (df_closed['resolution_time_hours'] > 0) & 
    (df_closed['resolution_time_hours'] < 365*24)  # Less than 1 year
].copy()

# Convert to days for easier interpretation
df_closed['resolution_time_days'] = df_closed['resolution_time_hours'] / 24

print(f"Closed cases: {len(df_closed):,}")
print(f"\nResolution time statistics (days):")
print(df_closed['resolution_time_days'].describe())

# Visualization
fig = px.histogram(df_closed, x='resolution_time_days', nbins=100,
                   title='Distribution of Resolution Time (Days)',
                   labels={'resolution_time_days': 'Days to Close'},
                   color_discrete_sequence=['#636EFA'])
fig.add_vline(x=df_closed['resolution_time_days'].median(), line_dash="dash", 
              annotation_text=f"Median: {df_closed['resolution_time_days'].median():.1f} days")
fig.update_xaxes(range=[0, 30])  # Focus on 0-30 days
fig.show()

Closed cases: 323,576

Resolution time statistics (days):
count    323576.000000
mean         57.194916
std          87.594128
min           0.000173
25%           2.071552
50%          10.626650
75%          76.727524
max         364.979187
Name: resolution_time_days, dtype: float64


## Step 3: Feature Engineering
Create features for ML model

In [9]:
# Extract temporal features from timestamp
df_closed['hour'] = df_closed['timestamp'].dt.hour
df_closed['is_business_hour'] = df_closed['hour'].between(9, 17).astype(int)

# Use external data features if available, otherwise create from timestamp
if 'year_ext' not in df_closed.columns:
    df_closed['year'] = df_closed['timestamp'].dt.year
    df_closed['month'] = df_closed['timestamp'].dt.month
    df_closed['day_of_week'] = df_closed['timestamp'].dt.dayofweek
    df_closed['quarter'] = df_closed['timestamp'].dt.quarter
else:
    # Use external data temporal features (already aligned)
    df_closed['year'] = df_closed['year_ext']
    df_closed['month'] = df_closed['month_ext']
    df_closed['day_of_week'] = df_closed['day_of_week_ext']
    df_closed['quarter'] = df_closed['quarter']

# Use is_weekend from external data if available
if 'is_weekend' not in df_closed.columns:
    df_closed['is_weekend'] = df_closed['day_of_week'].isin([5, 6]).astype(int)

# Calculate district workload (number of open cases at the time)
print("Calculating district workload...")
df_closed = df_closed.sort_values('timestamp')
df_closed['district_workload'] = df_closed.groupby('district').cumcount()

# Organization workload
df_closed['org_workload'] = df_closed.groupby('organization').cumcount()

# Historical avg resolution time by district (rolling)
df_closed['district_avg_resolution'] = df_closed.groupby('district')['resolution_time_days'].transform(
    lambda x: x.expanding().mean().shift(1)
)

# Fill NaN for first cases
df_closed['district_avg_resolution'] = df_closed['district_avg_resolution'].fillna(
    df_closed['resolution_time_days'].median()
)

# Base features (before adding external data)
feature_cols = ['year', 'month', 'hour', 'day_of_week', 'is_weekend', 
                'is_business_hour', 'quarter', 'district_workload', 'org_workload',
                'district_avg_resolution']

# Add external weather/environmental features if available
external_features = []
if 'pm25_avg' in df_closed.columns:
    df_closed['pm25_avg'] = df_closed['pm25_avg'].fillna(df_closed['pm25_avg'].median())
    external_features.append('pm25_avg')
    
if 'rainfall_mm' in df_closed.columns:
    df_closed['rainfall_mm'] = df_closed['rainfall_mm'].fillna(0)
    external_features.append('rainfall_mm')
    
if 'is_holiday' in df_closed.columns:
    df_closed['is_holiday'] = df_closed['is_holiday'].fillna(0).astype(int)
    external_features.append('is_holiday')
    
if 'weather_severity' in df_closed.columns:
    df_closed['weather_severity'] = df_closed['weather_severity'].fillna(0).astype(int)
    external_features.append('weather_severity')

feature_cols.extend(external_features)

print("\nFeatures created:")
print(f"  Temporal features: {len(feature_cols) - len(external_features)}")
print(f"  External features: {len(external_features)} - {external_features}")
print(f"  Total features: {len(feature_cols)}")

df_closed[feature_cols + ['resolution_time_days']].head(10)

Calculating district workload...

Features created:
  Temporal features: 10
  External features: 4 - ['pm25_avg', 'rainfall_mm', 'is_holiday', 'weather_severity']
  Total features: 14

Features created:
  Temporal features: 10
  External features: 4 - ['pm25_avg', 'rainfall_mm', 'is_holiday', 'weather_severity']
  Total features: 14


year  month  hour  day_of_week  is_weekend  is_business_hour  quarter  \
0      NaN    NaN    12          NaN         NaN                 1      NaN   
1      NaN    NaN    14          NaN         NaN                 1      NaN   
2      NaN    NaN     5          NaN         NaN                 0      NaN   
3      NaN    NaN    10          NaN         NaN                 1      NaN   
4      NaN    NaN    12          NaN         NaN                 1      NaN   
8      NaN    NaN    23          NaN         NaN                 0      NaN   
9      NaN    NaN    10          NaN         NaN                 1      NaN   
10     NaN    NaN    10          NaN         NaN                 1      NaN   
11     NaN    NaN     3          NaN         NaN                 0      NaN   
12  2022.0    1.0    10          6.0         1.0                 1      1.0   

    district_workload  org_workload  district_avg_resolution  pm25_avg  \
0                 0.0             0                10.626650     25.35   
1                 0.0             0                10.626650     25.35   
2                 0.0             0                10.626650     25.35   
3                 1.0             0               274.113254     25.35   
4                 0.0             0                10.626650     25.35   
8                 1.0             0               274.725701     25.35   
9                 2.0             1               229.518616     25.35   
10                3.0             2               213.053274     25.35   
11                4.0             0               229.520649     25.35   
12                1.0             0               252.842589     25.35   

    rainfall_mm  is_holiday  weather_severity  resolution_time_days  
0           0.0           0                 0            274.113254  
1           0.0           0                 0            274.725701  
2           0.0           0                 0            252.842589  
3           0.0           0                 0            328.909908  
4           0.0           0                 0            245.784450  
8           0.0           0                 0            184.311530  
9           0.0           0                 0            180.122589  
10          0.0           0                 0            278.922776  
11          0.0           0                 0            196.118707  
12          0.0           1                 0            156.786657

## Step 4: Encode Categorical Features
(External data already merged in Step 3)

In [10]:
# External data summary (already merged from traffy_with_external.csv)
print("📊 External Data Summary:")
print(f"  PM2.5 coverage: {df_closed['pm25_avg'].notna().sum():,} rows" if 'pm25_avg' in df_closed.columns else "  PM2.5: Not available")
print(f"  Rainfall coverage: {df_closed['rainfall_mm'].notna().sum():,} rows" if 'rainfall_mm' in df_closed.columns else "  Rainfall: Not available")
print(f"  Holiday data: {df_closed['is_holiday'].sum():,} cases on holidays/weekends" if 'is_holiday' in df_closed.columns else "  Holidays: Not available")
print(f"  Weekend data: {df_closed['is_weekend'].sum():,} cases on weekends" if 'is_weekend' in df_closed.columns else "  Weekends: Not available")

# Show sample of external features
if any(feat in df_closed.columns for feat in ['pm25_avg', 'rainfall_mm', 'is_holiday', 'weather_severity']):
    ext_cols = [col for col in ['timestamp', 'pm25_avg', 'rainfall_mm', 'is_holiday', 'is_weekend', 'weather_severity'] if col in df_closed.columns]
    print("\nSample external data:")
    display(df_closed[ext_cols].head(10))
else:
    print("\n⚠️ Warning: No external data found in merged dataset")

print(f"\n✓ Total features for model: {len(feature_cols)}")
print(f"  Features: {feature_cols}")

📊 External Data Summary:
  PM2.5 coverage: 323,576 rows
  Rainfall coverage: 323,576 rows
  Holiday data: 95,265 cases on holidays/weekends
  Weekend data: 80,929.0 cases on weekends

Sample external data:


timestamp  pm25_avg  rainfall_mm  is_holiday  \
0  2021-09-03 12:51:09.453003+00:00     25.35          0.0           0   
1  2021-09-19 14:56:08.924992+00:00     25.35          0.0           0   
2  2021-09-26 05:03:52.594898+00:00     25.35          0.0           0   
3  2021-10-14 10:45:27.713884+00:00     25.35          0.0           0   
4  2021-12-09 12:29:08.408763+00:00     25.35          0.0           0   
8  2021-12-21 23:03:58.450912+00:00     25.35          0.0           0   
9  2021-12-22 10:15:33.294829+00:00     25.35          0.0           0   
10 2021-12-23 10:26:48.868250+00:00     25.35          0.0           0   
11 2021-12-28 03:59:06.003252+00:00     25.35          0.0           0   
12 2022-01-02 10:53:25.580723+00:00     25.35          0.0           1   

    is_weekend  weather_severity  
0          NaN                 0  
1          NaN                 0  
2          NaN                 0  
3          NaN                 0  
4          NaN                 0  
8          NaN                 0  
9          NaN                 0  
10         NaN                 0  
11         NaN                 0  
12         1.0                 0


✓ Total features for model: 14
  Features: ['year', 'month', 'hour', 'day_of_week', 'is_weekend', 'is_business_hour', 'quarter', 'district_workload', 'org_workload', 'district_avg_resolution', 'pm25_avg', 'rainfall_mm', 'is_holiday', 'weather_severity']


## Step 5: Encode Categorical Features

In [11]:
# Select important categorical columns
categorical_cols = ['type', 'organization', 'district']

# Label encoding for tree-based models
label_encoders = {}
for col in categorical_cols:
    le = LabelEncoder()
    df_closed[f'{col}_encoded'] = le.fit_transform(df_closed[col].astype(str))
    label_encoders[col] = le
    print(f"{col}: {len(le.classes_)} unique values")

# Add encoded features to feature list
feature_cols.extend([f'{col}_encoded' for col in categorical_cols])

print(f"\nFinal feature count: {len(feature_cols)}")
print(f"Features: {feature_cols}")

type: 8261 unique values
organization: 31720 unique values
district: 86 unique values

Final feature count: 17
Features: ['year', 'month', 'hour', 'day_of_week', 'is_weekend', 'is_business_hour', 'quarter', 'district_workload', 'org_workload', 'district_avg_resolution', 'pm25_avg', 'rainfall_mm', 'is_holiday', 'weather_severity', 'type_encoded', 'organization_encoded', 'district_encoded']
organization: 31720 unique values
district: 86 unique values

Final feature count: 17
Features: ['year', 'month', 'hour', 'day_of_week', 'is_weekend', 'is_business_hour', 'quarter', 'district_workload', 'org_workload', 'district_avg_resolution', 'pm25_avg', 'rainfall_mm', 'is_holiday', 'weather_severity', 'type_encoded', 'organization_encoded', 'district_encoded']


## Step 6: Prepare Train/Test Split

In [12]:
# Remove rows with missing features
df_model = df_closed[feature_cols + ['resolution_time_days', 'district', 'latitude', 'longitude']].dropna()

print(f"Final dataset size: {len(df_model):,} rows")

# Prepare X and y
X = df_model[feature_cols]
y = df_model['resolution_time_days']

# Train/test split (80/20, time-based to avoid data leakage)
split_date = df_closed['timestamp'].quantile(0.8)
train_mask = df_closed['timestamp'] <= split_date
test_mask = df_closed['timestamp'] > split_date

X_train = df_model.loc[df_closed.loc[df_model.index, 'timestamp'] <= split_date, feature_cols]
X_test = df_model.loc[df_closed.loc[df_model.index, 'timestamp'] > split_date, feature_cols]
y_train = df_model.loc[df_closed.loc[df_model.index, 'timestamp'] <= split_date, 'resolution_time_days']
y_test = df_model.loc[df_closed.loc[df_model.index, 'timestamp'] > split_date, 'resolution_time_days']

print(f"\nTrain set: {len(X_train):,} samples")
print(f"Test set: {len(X_test):,} samples")
print(f"Split date: {split_date}")

Final dataset size: 323,354 rows

Train set: 258,639 samples
Test set: 64,715 samples
Split date: 2023-07-18 05:55:44.221028096+00:00


## Step 7: Train XGBoost Model

In [13]:
# Train XGBoost model
print("Training XGBoost model...")
model = xgb.XGBRegressor(
    n_estimators=200,
    max_depth=8,
    learning_rate=0.1,
    random_state=42,
    n_jobs=-1
)

model.fit(X_train, y_train)

# Predictions
y_pred_train = model.predict(X_train)
y_pred_test = model.predict(X_test)

# Evaluation metrics
train_mae = mean_absolute_error(y_train, y_pred_train)
test_mae = mean_absolute_error(y_test, y_pred_test)
train_rmse = np.sqrt(mean_squared_error(y_train, y_pred_train))
test_rmse = np.sqrt(mean_squared_error(y_test, y_pred_test))
train_r2 = r2_score(y_train, y_pred_train)
test_r2 = r2_score(y_test, y_pred_test)

print("\n" + "="*60)
print("MODEL PERFORMANCE")
print("="*60)
print(f"\nTrain Set:")
print(f"  MAE:  {train_mae:.2f} days")
print(f"  RMSE: {train_rmse:.2f} days")
print(f"  R²:   {train_r2:.4f}")

print(f"\nTest Set:")
print(f"  MAE:  {test_mae:.2f} days")
print(f"  RMSE: {test_rmse:.2f} days")
print(f"  R²:   {test_r2:.4f}")

print("\n" + "="*60)

Training XGBoost model...

MODEL PERFORMANCE

Train Set:
  MAE:  40.76 days
  RMSE: 61.34 days
  R²:   0.5334

Test Set:
  MAE:  47.74 days
  RMSE: 69.92 days
  R²:   0.1766



## Step 8: Feature Importance Analysis

In [14]:
# Feature importance
feature_importance = pd.DataFrame({
    'feature': feature_cols,
    'importance': model.feature_importances_
}).sort_values('importance', ascending=False)

print("Top 15 Most Important Features:")
print(feature_importance.head(15))

# Visualization
fig = px.bar(feature_importance.head(15), 
             x='importance', y='feature',
             orientation='h',
             title='Top 15 Feature Importance (XGBoost)',
             labels={'importance': 'Importance Score', 'feature': 'Feature'},
             color='importance',
             color_continuous_scale='Blues')
fig.update_layout(yaxis={'categoryorder': 'total ascending'})
fig.show()

Top 15 Most Important Features:
                    feature  importance
9   district_avg_resolution    0.247722
8              org_workload    0.112953
1                     month    0.105585
15     organization_encoded    0.094564
0                      year    0.092054
14             type_encoded    0.068949
16         district_encoded    0.062642
7         district_workload    0.059493
10                 pm25_avg    0.029820
13         weather_severity    0.026194
11              rainfall_mm    0.023609
12               is_holiday    0.021678
5          is_business_hour    0.019393
2                      hour    0.018266
3               day_of_week    0.017079


## Step 9: Model Predictions Visualization

In [15]:
# Scatter plot: Actual vs Predicted
comparison_df = pd.DataFrame({
    'Actual': y_test,
    'Predicted': y_pred_test
})

fig = px.scatter(comparison_df, x='Actual', y='Predicted',
                 title='Actual vs Predicted Resolution Time (Test Set)',
                 labels={'Actual': 'Actual Days', 'Predicted': 'Predicted Days'},
                 opacity=0.5)
# Add perfect prediction line
max_val = max(comparison_df['Actual'].max(), comparison_df['Predicted'].max())
fig.add_trace(go.Scatter(x=[0, max_val], y=[0, max_val], 
                         mode='lines', name='Perfect Prediction',
                         line=dict(color='red', dash='dash')))
fig.update_xaxes(range=[0, 30])
fig.update_yaxes(range=[0, 30])
fig.show()

# Residuals plot
comparison_df['Residuals'] = comparison_df['Actual'] - comparison_df['Predicted']
fig = px.histogram(comparison_df, x='Residuals', nbins=50,
                   title='Distribution of Prediction Errors',
                   labels={'Residuals': 'Error (Actual - Predicted) in Days'})
fig.add_vline(x=0, line_dash="dash", annotation_text="Zero Error")
fig.show()

## Step 10: Geographic Analysis - Slow vs Fast Districts

In [16]:
# Calculate average resolution time by district
district_stats = df_closed.groupby('district').agg({
    'resolution_time_days': ['mean', 'median', 'std', 'count'],
    'latitude': 'mean',
    'longitude': 'mean'
}).reset_index()

district_stats.columns = ['district', 'avg_resolution_days', 'median_resolution_days', 
                          'std_resolution', 'case_count', 'lat', 'lon']

# Filter districts with at least 100 cases
district_stats = district_stats[district_stats['case_count'] >= 100]

# Sort by average resolution time
district_stats = district_stats.sort_values('avg_resolution_days', ascending=False)

print("Top 10 SLOWEST Districts (Average Resolution Time):")
print(district_stats[['district', 'avg_resolution_days', 'case_count']].head(10))

print("\nTop 10 FASTEST Districts:")
print(district_stats[['district', 'avg_resolution_days', 'case_count']].tail(10))

# Bar chart
fig = px.bar(district_stats.head(20), 
             x='avg_resolution_days', y='district',
             orientation='h',
             title='Top 20 Slowest Districts (Average Resolution Time)',
             labels={'avg_resolution_days': 'Average Days to Close', 'district': 'District'},
             color='avg_resolution_days',
             color_continuous_scale='Reds',
             hover_data=['case_count'])
fig.update_layout(yaxis={'categoryorder': 'total ascending'})
fig.show()

Top 10 SLOWEST Districts (Average Resolution Time):
      district  avg_resolution_days  case_count
63     สวนหลวง           133.683401        8622
56   ลาดกระบัง           122.954633        7565
33      บางรัก           110.868521        5987
7      จตุจักร            99.384966       15593
73    ห้วยขวาง            79.229779        5995
20  บางกอกน้อย            74.298318        6948
69     หนองจอก            72.002749        5615
64    สะพานสูง            69.786884        5549
26       บางนา            67.402652        6245
3    คลองสามวา            64.745421        6665

Top 10 FASTEST Districts:
       district  avg_resolution_days  case_count
35       บางเขน            36.889745       10420
17       ธนบุรี            36.643046        6578
37        บางแค            33.103287       12089
15      ทุ่งครุ            32.516140        3937
55  ราษฎร์บูรณะ            32.005944        3312
10     ดอนเมือง            31.690096        4831
57     ลาดพร้าว            31.672948        6655
2

## Step 11: Interactive Heatmap - Bangkok Districts

In [17]:
# Geographic heatmap of resolution time
fig = px.scatter_mapbox(district_stats, 
                        lat='lat', lon='lon',
                        color='avg_resolution_days',
                        size='case_count',
                        hover_name='district',
                        hover_data={'avg_resolution_days': ':.2f',
                                   'median_resolution_days': ':.2f',
                                   'case_count': ':,',
                                   'lat': False,
                                   'lon': False},
                        title='Bangkok Districts: Average Resolution Time (Heatmap)',
                        mapbox_style='open-street-map',
                        zoom=10,
                        height=700,
                        color_continuous_scale='RdYlGn_r',  # Red = slow, Green = fast
                        size_max=30)

fig.update_layout(
    coloraxis_colorbar=dict(title="Avg Days"),
    mapbox=dict(center=dict(lat=13.75, lon=100.50))
)

fig.show()

print("\n🗺️ Red circles = Slow response districts (need support)")
print("🗺️ Green circles = Fast response districts")
print("🗺️ Circle size = Number of cases handled")


🗺️ Red circles = Slow response districts (need support)
🗺️ Green circles = Fast response districts
🗺️ Circle size = Number of cases handled


## Step 12: Time-based Analysis (Monthly Trends)

In [18]:
# Monthly resolution time trends
df_closed['year_month'] = df_closed['timestamp'].dt.to_period('M').astype(str)

monthly_stats = df_closed.groupby('year_month').agg({
    'resolution_time_days': ['mean', 'median', 'count']
}).reset_index()

monthly_stats.columns = ['year_month', 'avg_days', 'median_days', 'case_count']

# Line chart
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=monthly_stats['year_month'],
    y=monthly_stats['avg_days'],
    mode='lines+markers',
    name='Average',
    line=dict(color='#636EFA', width=3)
))

fig.add_trace(go.Scatter(
    x=monthly_stats['year_month'],
    y=monthly_stats['median_days'],
    mode='lines+markers',
    name='Median',
    line=dict(color='#EF553B', width=2, dash='dash')
))

fig.update_layout(
    title='Resolution Time Trends Over Time',
    xaxis_title='Month',
    yaxis_title='Days to Close',
    hovermode='x unified',
    height=500
)

fig.show()

## Step 13: Save Model and Feature Pipeline

In [19]:
import pickle

# Save model
model_path = "../models/fixtime_xgboost_model.pkl"
with open(model_path, 'wb') as f:
    pickle.dump(model, f)
print(f"✓ Model saved to: {model_path}")

# Save label encoders
encoder_path = "../models/label_encoders.pkl"
with open(encoder_path, 'wb') as f:
    pickle.dump(label_encoders, f)
print(f"✓ Label encoders saved to: {encoder_path}")

# Save feature list
feature_path = "../models/feature_list.pkl"
with open(feature_path, 'wb') as f:
    pickle.dump(feature_cols, f)
print(f"✓ Feature list saved to: {feature_path}")

# Save district statistics for dashboard
district_stats.to_csv("../data/processed/district_resolution_stats.csv", index=False)
print(f"✓ District stats saved to: ../data/processed/district_resolution_stats.csv")

✓ Model saved to: ../models/fixtime_xgboost_model.pkl
✓ Label encoders saved to: ../models/label_encoders.pkl
✓ Feature list saved to: ../models/feature_list.pkl
✓ District stats saved to: ../data/processed/district_resolution_stats.csv


## Step 14: Example Prediction Function

In [20]:
def predict_resolution_time(case_data, model, label_encoders, feature_cols):
    """
    Predict resolution time for a new case
    
    Parameters:
    - case_data: dict with keys matching required features
    - model: trained XGBoost model
    - label_encoders: dict of LabelEncoders
    - feature_cols: list of feature column names
    
    Returns:
    - predicted_days: float
    """
    # Create feature vector
    features = {}
    
    # Encode categorical features
    for col in ['type', 'organization', 'district']:
        if col in case_data:
            features[f'{col}_encoded'] = label_encoders[col].transform([case_data[col]])[0]
    
    # Add other features
    for col in feature_cols:
        if col not in features and col in case_data:
            features[col] = case_data[col]
    
    # Create DataFrame with correct column order
    X_new = pd.DataFrame([features], columns=feature_cols)
    
    # Predict
    prediction = model.predict(X_new)[0]
    
    return prediction

# Example usage - Get real values from data
sample_row = df_closed.iloc[100]  # Use a real case from dataset

example_case = {
    'type': sample_row['type'],
    'organization': sample_row['organization'],
    'district': sample_row['district'],
    'month': 6,
    'hour': 14,
    'day_of_week': 2,
    'is_weekend': 0,
    'is_business_hour': 1,
    'is_holiday': 0,
    'quarter': 2,
    'district_workload': 50,
    'org_workload': 100,
    'district_avg_resolution': 5.5,
    'days_since_holiday': 7,
    'year': 2024,
    'day': 15
}

print(f"Using real data example:")
print(f"  Type: {example_case['type']}")
print(f"  Organization: {example_case['organization']}")
print(f"  District: {example_case['district']}")

predicted_days = predict_resolution_time(example_case, model, label_encoders, feature_cols)
print(f"\n📊 Example Prediction:")
print(f"Case Type: {example_case['type']}")
print(f"District: {example_case['district']}")
print(f"Organization: {example_case['organization']}")
print(f"\n⏱️ Predicted Resolution Time: {predicted_days:.1f} days")

if predicted_days > 7:
    print("⚠️ Warning: Expected to take more than 1 week!")
elif predicted_days > 3:
    print("⚡ Moderate priority")
else:
    print("✅ Expected to resolve quickly")

# Show available categories
print(f"\n📋 Available categories in model:")
print(f"Types: {', '.join(label_encoders['type'].classes_[:10])}... ({len(label_encoders['type'].classes_)} total)")
print(f"Organizations: {', '.join(label_encoders['organization'].classes_[:10])}... ({len(label_encoders['organization'].classes_)} total)")
print(f"Districts: {', '.join(label_encoders['district'].classes_[:10])}... ({len(label_encoders['district'].classes_)} total)")
print("✅ Expected to resolve quickly")

Using real data example:
  Type: {ความสะอาด}
  Organization: เขตดินแดง,ผอ.เขตดินแดง (นายชูชาติ),กลุ่มกรุงเทพกลาง (นายสุขสันต์ กิตติศุภกร)
  District: ดินแดง

📊 Example Prediction:
Case Type: {ความสะอาด}
District: ดินแดง
Organization: เขตดินแดง,ผอ.เขตดินแดง (นายชูชาติ),กลุ่มกรุงเทพกลาง (นายสุขสันต์ กิตติศุภกร)

⏱️ Predicted Resolution Time: 0.6 days
✅ Expected to resolve quickly

📋 Available categories in model:
Types: nan, {PM2.5,การเดินทาง,ถนน}, {PM2.5,กีดขวาง,ถนน}, {PM2.5,กีดขวาง,ทางเท้า,จราจร}, {PM2.5,กีดขวาง,ทางเท้า}, {PM2.5,กีดขวาง}, {PM2.5,คลอง,ความสะอาด}, {PM2.5,คลอง,ถนน}, {PM2.5,คลอง}, {PM2.5,ความปลอดภัย,จราจร}... (8261 total)
Organizations: 1111 ศูนย์รับเรื่องราวร้องทุกข์ของรัฐบาล,เขตดุสิต, 1111 ศูนย์รับเรื่องราวร้องทุกข์ของรัฐบาล,เขตดุสิต,ผอ.เขตดุสิต (น.ส.รุจิรา),กลุ่มกรุงเทพกลาง (นายสุขสันต์ กิตติศุภกร), 1111 ศูนย์รับเรื่องราวร้องทุกข์ของรัฐบาล,เขตดุสิต,สำนักการโยธา กทม.,ผอ.เขตดุสิต (น.ส.รุจิรา),กลุ่มกรุงเทพกลาง (นายสุขสันต์ กิตติศุภกร), 1111 ศูนย์รับเรื่องราวร้องทุกข์ของรัฐ

## Step 15: Final Summary Report

In [22]:
print("="*80)
print("FIXTIME AI - FINAL SUMMARY REPORT")
print("="*80)

print("\n📊 DATASET STATISTICS")
print(f"   Total closed cases analyzed: {len(df_closed):,}")
print(f"   Date range: {df_closed['timestamp'].min().date()} to {df_closed['timestamp'].max().date()}")
print(f"   Average resolution time: {df_closed['resolution_time_days'].mean():.2f} days")
print(f"   Median resolution time: {df_closed['resolution_time_days'].median():.2f} days")

print("\n🤖 MODEL PERFORMANCE")
print(f"   Algorithm: XGBoost Regression")
print(f"   Test MAE: {test_mae:.2f} days")
print(f"   Test RMSE: {test_rmse:.2f} days")
print(f"   Test R²: {test_r2:.4f}")
print(f"   Number of features: {len(feature_cols)}")

print("\n🗺️ GEOGRAPHIC INSIGHTS")
slowest = district_stats.iloc[0]
fastest = district_stats.iloc[-1]
print(f"   Slowest district: {slowest['district']} ({slowest['avg_resolution_days']:.2f} days avg)")
print(f"   Fastest district: {fastest['district']} ({fastest['avg_resolution_days']:.2f} days avg)")
print(f"   Districts analyzed: {len(district_stats)}")

print("\n🌐 EXTERNAL DATA INTEGRATION")
if 'pm25_avg' in df_closed.columns:
    print(f"   PM2.5 avg: {df_closed['pm25_avg'].mean():.2f} μg/m³")
if 'rainfall_mm' in df_closed.columns:
    print(f"   Avg daily rainfall: {df_closed['rainfall_mm'].mean():.2f} mm")
if 'is_holiday' in df_closed.columns:
    print(f"   Cases on holidays/weekends: {df_closed['is_holiday'].sum():,}")

print("\n💾 OUTPUT FILES")
print(f"   ✓ {model_path}")
print(f"   ✓ {encoder_path}")
print(f"   ✓ {feature_path}")
print(f"   ✓ ../data/processed/district_resolution_stats.csv")

print("\n🎯 KEY RECOMMENDATIONS")
print("   1. Prioritize resources to top 5 slowest districts")
print("   2. Investigate workload patterns in high-backlog areas")
print("   3. Monitor resolution time trends monthly")
print("   4. Use model predictions for resource allocation")

print("\n" + "="*80)
print("🎉 FixTime AI Analysis Complete!")
print("="*80)

FIXTIME AI - FINAL SUMMARY REPORT

📊 DATASET STATISTICS
   Total closed cases analyzed: 323,576
   Date range: 2021-09-03 to 2023-10-24
   Average resolution time: 57.19 days
   Median resolution time: 10.63 days

🤖 MODEL PERFORMANCE
   Algorithm: XGBoost Regression
   Test MAE: 47.74 days
   Test RMSE: 69.92 days
   Test R²: 0.1766
   Number of features: 17

🗺️ GEOGRAPHIC INSIGHTS
   Slowest district: สวนหลวง (133.68 days avg)
   Fastest district: สัมพันธวงศ์ (25.77 days avg)
   Districts analyzed: 50

🌐 EXTERNAL DATA INTEGRATION
   PM2.5 avg: 35.10 μg/m³
   Avg daily rainfall: 6.69 mm
   Cases on holidays/weekends: 95,265

💾 OUTPUT FILES
   ✓ ../models/fixtime_xgboost_model.pkl
   ✓ ../models/label_encoders.pkl
   ✓ ../models/feature_list.pkl
   ✓ ../data/processed/district_resolution_stats.csv

🎯 KEY RECOMMENDATIONS
   1. Prioritize resources to top 5 slowest districts
   2. Investigate workload patterns in high-backlog areas
   3. Monitor resolution time trends monthly
   4. Use mo